##### Copyright 2020 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Keras Tuner の基礎

<table class="tfo-notebook-buttons" align="left">
  <td> <img src="https://www.tensorflow.org/images/tf_logo_32px.png"><a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ja/tutorials/keras/keras_tuner.ipynb">TensorFlow.org で表示</a> </td>
  <td> <img src="https://www.tensorflow.org/images/colab_logo_32px.png"><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ja/tutorials/keras/keras_tuner.ipynb">Google Colab で実行</a> </td>
  <td> <img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png"><a target="_blank" href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ja/tutorials/keras/keras_tuner.ipynb">GitHub でソースを表示</a> </td>
  <td> <img src="https://www.tensorflow.org/images/download_logo_32px.png"><a href="https://storage.googleapis.com/tensorflow_docs/docs/site/en/tutorials/keras/keras_tuner.ipynb">ノートブックをダウンロード</a> </td>
</table>

## 概要

Keras Tuner は、TensorFlow プログラム向けに最適なハイパーパラメータを選択するためのライブラリです。ユーザーの機械学習（ML）アプリケーションに適切なハイパーパラメータを選択するためのプロセスは、*ハイパーパラメータチューニング*または*ハイパーチューニング*と呼ばれます。

ハイパーパラメータは、ML のトレーニングプロセスとトポロジーを管理する変数です。これらの変数はトレーニングプロセス中、一貫して定数を維持し、ML プログラムのパフォーマンスに直接影響を与えます。ハイパーパラメータには、以下の 2 種類があります。

1. **モデルハイパーパラメータ**: 非表示レイヤーの数と幅などのモデルの選択に影響します。
2. **アルゴリズムハイパーパラメータ**: 確率的勾配降下法 (SGD) の学習率や k 最近傍 (KNN) 分類器の最近傍の数など、学習アルゴリズムの速度と質に影響します。

このチュートリアルでは、Keras Tuner を使用して、画像分類アプリケーションのハイパーチューニングを実施します。

## セットアップ

In [2]:
import tensorflow as tf
from tensorflow import keras

2022-12-15 00:15:50.634115: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-15 00:15:50.634212: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-15 00:15:50.634221: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


Keras Tuner をインストールしてインポートします。

In [3]:
!pip install -q -U keras-tuner

In [4]:
import keras_tuner as kt

## データセットをダウンロードして準備する

このチュートリアルでは、Keras Tuner を使用して、[Fashion MNIST データセット](https://github.com/zalandoresearch/fashion-mnist)の服飾の画像を分類する学習モデル向けに最適なハイパーパラメータを見つけます。

データを読み込みます。

In [5]:
(img_train, label_train), (img_test, label_test) = keras.datasets.fashion_mnist.load_data()

In [6]:
# Normalize pixel values between 0 and 1
img_train = img_train.astype('float32') / 255.0
img_test = img_test.astype('float32') / 255.0

## モデルを定義する

ハイパーチューニングを行うモデルを構築する際、モデルアーキテクチャのほかにハイパーパラメータ検索空間も定義します。ハイパーチューニング用にセットアップするモデルを*ハイパーモデル*と呼びます。

ハイパーモデルの定義は、以下の 2 つの方法で行います。

- モデルビルダー関数を使用する
- Keras Tuner API の `HyperModel` クラスをサブクラス化する

また、コンピュータビジョンアプリケーション用の [HyperXception](https://keras.io/api/keras_tuner/hypermodels/) と [HyperResNet](https://keras.io/api/keras_tuner/hypermodels/hyper_xception/) という 2 つの事前定義済みの <code>HyperModel</code> クラスも使用します。

このチュートリアルでは、モデルビルダー関数を使用して、画像分類モデルを定義します。モデルビルダー関数は、コンパイル済みのモデルを返し、インラインで定義するハイパーパラメータを使用してモデルをハイパーチューニングします。

In [7]:
def model_builder(hp):
  model = keras.Sequential()
  model.add(keras.layers.Flatten(input_shape=(28, 28)))

  # Tune the number of units in the first Dense layer
  # Choose an optimal value between 32-512
  hp_units = hp.Int('units', min_value=32, max_value=512, step=32)
  model.add(keras.layers.Dense(units=hp_units, activation='relu'))
  model.add(keras.layers.Dense(10))

  # Tune the learning rate for the optimizer
  # Choose an optimal value from 0.01, 0.001, or 0.0001
  hp_learning_rate = hp.Choice('learning_rate', values=[1e-2, 1e-3, 1e-4])

  model.compile(optimizer=keras.optimizers.Adam(learning_rate=hp_learning_rate),
                loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
                metrics=['accuracy'])

  return model

## チューナーをインスタンス化してハイパーチューニングを実行する

チューナーをインスタンス化して、ハイパーチューニングを実行します。Keras Tuner には、`RandomSearch`、`Hyperband`、`BayesianOptimization`、および `Sklearn` チューナーがあります。このチュートリアルでは、[Hyperband](https://arxiv.org/pdf/1603.06560.pdf) チューナーを使用します。

Hyperband チューナーをインスタンス化するには、ハイパーモデル、最適化する `objective`、およびトレーニングするエポックの最大数 (`max_epochs`) を指定する必要があります。

In [8]:
tuner = kt.Hyperband(model_builder,
                     objective='val_accuracy',
                     max_epochs=10,
                     factor=3,
                     directory='my_dir',
                     project_name='intro_to_kt')

Hyperband チューニングアルゴリズムは、適応型リソース割り当てと早期停止を使用して、高パフォーマンスモデルに素早く収束させます。これは、トーナメント式のツリーを使用して行われます。アルゴリズムは、数回のエポックで大量のモデルをトレーニングし、性能の高い上位半数のモデル次のラウンドに持ち越します。Hyperband は、1 + log<sub><code>factor</code></sub>(`max_epochs`) を計算し、直近の整数に繰り上げて、トーナメントでトレーニングするモデル数を決定します。

検証損失の特定の値に達した後、トレーニングを早期に停止するためのコールバックを作成します。

In [9]:
stop_early = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=5)

ハイパーパラメータ検索を実行します。検索メソッドの引数は、上記のコールバックのほか、`tf.keras.model.fit` に使用される引数と同じです。

In [10]:
tuner.search(img_train, label_train, epochs=50, validation_split=0.2, callbacks=[stop_early])

# Get the optimal hyperparameters
best_hps=tuner.get_best_hyperparameters(num_trials=1)[0]

print(f"""
The hyperparameter search is complete. The optimal number of units in the first densely-connected
layer is {best_hps.get('units')} and the optimal learning rate for the optimizer
is {best_hps.get('learning_rate')}.
""")

Trial 30 Complete [00h 00m 41s]
val_accuracy: 0.890999972820282

Best val_accuracy So Far: 0.890999972820282
Total elapsed time: 00h 08m 39s
INFO:tensorflow:Oracle triggered exit



The hyperparameter search is complete. The optimal number of units in the first densely-connected
layer is 352 and the optimal learning rate for the optimizer
is 0.001.



## モデルをトレーニングする

検索から取得したハイパーパラメータを使用してモデルをトレーニングするための最適なエポック数を見つけます。

In [11]:
# Build the model with the optimal hyperparameters and train it on the data for 50 epochs
model = tuner.hypermodel.build(best_hps)
history = model.fit(img_train, label_train, epochs=50, validation_split=0.2)

val_acc_per_epoch = history.history['val_accuracy']
best_epoch = val_acc_per_epoch.index(max(val_acc_per_epoch)) + 1
print('Best epoch: %d' % (best_epoch,))

Epoch 1/50


   1/1500 [..............................] - ETA: 19:12 - loss: 2.5375 - accuracy: 0.0625

  25/1500 [..............................] - ETA: 3s - loss: 1.3828 - accuracy: 0.5263   

  48/1500 [..............................] - ETA: 3s - loss: 1.1110 - accuracy: 0.6048

  71/1500 [>.............................] - ETA: 3s - loss: 0.9800 - accuracy: 0.6496

...

1438/1500 [===========================>..] - ETA: 0s - loss: 0.0735 - accuracy: 0.9723

1461/1500 [============================>.] - ETA: 0s - loss: 0.0735 - accuracy: 0.9724

1484/1500 [============================>.] - ETA: 0s - loss: 0.0736 - accuracy: 0.9723

1500/1500 [==============================] - 4s 3ms/step - loss: 0.0735 - accuracy: 0.9723 - val_loss: 0.5423 - val_accuracy: 0.8962


Best epoch: 26


ハイパーモデルを再インスタンス化し、前述の最適なエポック数でトレーニングします。

In [12]:
hypermodel = tuner.hypermodel.build(best_hps)

# Retrain the model
hypermodel.fit(img_train, label_train, epochs=best_epoch, validation_split=0.2)

Epoch 1/26


   1/1500 [..............................] - ETA: 19:52 - loss: 2.4265 - accuracy: 0.1250

  25/1500 [..............................] - ETA: 3s - loss: 1.2743 - accuracy: 0.5475   

  50/1500 [>.............................] - ETA: 3s - loss: 1.0539 - accuracy: 0.6344

  75/1500 [>.............................] - ETA: 2s - loss: 0.9471 - accuracy: 0.6750

...

1421/1500 [===========================>..] - ETA: 0s - loss: 0.1313 - accuracy: 0.9513

1445/1500 [===========================>..] - ETA: 0s - loss: 0.1311 - accuracy: 0.9514

1468/1500 [============================>.] - ETA: 0s - loss: 0.1320 - accuracy: 0.9511

1492/1500 [============================>.] - ETA: 0s - loss: 0.1328 - accuracy: 0.9506

1500/1500 [==============================] - 4s 3ms/step - loss: 0.1328 - accuracy: 0.9506 - val_loss: 0.3717 - val_accuracy: 0.8923


このチュートリアルを終了するには、テストデータでハイパーモデルを評価します。

In [13]:
eval_result = hypermodel.evaluate(img_test, label_test)
print("[test loss, test accuracy]:", eval_result)

  1/313 [..............................] - ETA: 45s - loss: 0.6250 - accuracy: 0.8750

 29/313 [=>............................] - ETA: 0s - loss: 0.4126 - accuracy: 0.8933 

 56/313 [====>.........................] - ETA: 0s - loss: 0.3725 - accuracy: 0.8929

 84/313 [=======>......................] - ETA: 0s - loss: 0.3768 - accuracy: 0.8906

112/313 [=========>....................] - ETA: 0s - loss: 0.4116 - accuracy: 0.8853

...

253/313 [=======================>......] - ETA: 0s - loss: 0.4208 - accuracy: 0.8864

281/313 [=========================>....] - ETA: 0s - loss: 0.4201 - accuracy: 0.8861

310/313 [============================>.] - ETA: 0s - loss: 0.4132 - accuracy: 0.8875

313/313 [==============================] - 1s 2ms/step - loss: 0.4146 - accuracy: 0.8872


[test loss, test accuracy]: [0.4146318733692169, 0.8871999979019165]


`my_dir/intro_to_kt` ディレクトリには、ハイパーパラメータ検索中に実行された各トライアル（モデル構成）の詳細なログとチェックポイントが含まれます。ハイパーパラメータ検索を再実行する場合、Keras Tuner は、これらのログの既存の状態を使用して、検索を再開します。この動作を無効にするには、チューナーをインスタンス化する際に、`overwrite = True` 引数を追加で渡してください。

## まとめ

このチュートリアルでは、Keras Tuner の使用して、モデルのハイパーパラメータを調整する方法を学習しました。Keras Tuner の調査委については、以下のその他のリソースをご覧ください。

- [TensorFlow ブログの KerasTuner](https://blog.tensorflow.org/2020/01/hyperparameter-tuning-with-keras-tuner.html)
- [KerasTuner の Web サイト](https://keras-team.github.io/keras-tuner/)

また、モデルのハイパーパラメータを対話式で調整できる、TensorBoard の [HParams Dashboard](https://www.tensorflow.org/tensorboard/hyperparameter_tuning_with_hparams) もご覧ください。